## Setup Code

In [ ]:
!pip install -q kaggle
!pip install pyyaml h5py
!mkdir ~/.kaggle
!chmod 600 ~/.kaggle
# For training, we will use a dataset consisting of 100 images designed for super resolution.
# The dataset can be found here: https://www.kaggle.com/datasets/akhileshdkapse/super-image-resolution
!echo "{\"username\":\"YOUR_KAGGLE_USERNAME_HERE!\",\"key\":\"YOUR_KAGGLE_KEY_HERE!\"}" > ~/.kaggle/kaggle.json
!kaggle datasets download -d akhileshdkapse/super-image-resolution
!mv ./super-image-resolution.zip ./data.zip

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
 92% 25.0M/27.2M [00:01<00:00, 24.3MB/s]
100% 27.2M/27.2M [00:01<00:00, 17.2MB/s]


In [ ]:
import os
from zipfile import ZipFile
from tqdm import tqdm

def setup():
    # Let's specify the assignment path we will be working with as the root.
    root_dir = os.path.join('./')
    data_dir = os.path.join(root_dir, 'data')
    os.makedirs(data_dir, exist_ok=True)

    # Open the .zip file and extract all folders into the './Data/images/' folder.
    with ZipFile("./data.zip", 'r') as data:
        for info in tqdm(iterable=data.infolist(), total=len(data.infolist()),\
                         unit="B", unit_scale=True, desc="Extracting .zip file"):
            info.filename = info.filename.replace('Data/', '')
            data.extract(info, os.path.join(data_dir, 'images'))
    return root_dir

In [ ]:
# High/low-resolution images located at 'data/images/HR' and 'data/images/LR/' 
# respectively.
root_dir = setup()

Extracting .zip file: 100%|██████████| 200/200 [00:00<00:00, 939B/s]


### Define Utility Functions

In [ ]:
import torch
import numpy as np
from torchvision import transforms

def tensor_to_image(image):
    'Converts a PyTorch tensor to a clipped numpy image.'
    tensor_image = image.clone().detach()
    image = tensor_image.permute(1, 2, 0).numpy()
    image = np.clip(image * 255, 0, 255).astype(np.uint8)
    
    return image



# Peak signal-to-noise ratio (PSNR) is the metric we use for image quality assessment.
def psnr(pred, label):
    'Calculates the peak signal-to-noise ratio between'
    mse = torch.mean((pred - label)**2)
    return 10 * torch.log10(1 / mse)



def ssim(pred, label):
    return structural_similarity_index_measure(pred, label)

### Define Super Resolution Dataset

In [ ]:
import torch
import os
import h5py
from torch.utils.data import Dataset
from torchvision import transforms
from torchvision.transforms import InterpolationMode
from PIL import Image

class SuperResolution(Dataset):
    'Super Resolution dataset for PyTorch'
    def __init__(self, root_dir, split='train'):
        assert split in ['train', 'val']
        self.h5_dataset = split + '.h5'

    def __len__(self):
        'Denotes the total number of samples'
        with h5py.File(self.h5_dataset, 'r') as dataset:
            return len(dataset['lr'])

    def __getitem__(self, index):
        'Generates one sample of data'
        with h5py.File(self.h5_dataset, 'r') as dataset:
            return torch.from_numpy(dataset['lr'][index]),\
                   torch.from_numpy(dataset['hr'][index])

##### **Dataset Preperation**
The h5py package is a Pythonic interface to the HDF5 binary data format. Converting our image files into the HDF5 format yields a vastly more efficient sample retrieval during our training process (often 4-5x reduced training time alone).

In [ ]:
import numpy as np
import h5py
import os
from torchvision import transforms
from torchvision.transforms import InterpolationMode
from PIL import Image

# The h5py package is a Pythonic interface to the HDF5 binary data format.
# Converting our image files into the HDF5 format yields a vastly more efficient
# sample retrieval during our training process.
#   * This yields about a 4-5x performance increase alone.
def create_h5_dataset(root_dir, image_dir, split='train', scale=4):
    assert split in ['train', 'val']

    try:
        # Remove previous .h5 file if it exists
        os.remove(os.path.join(root_dir, split + '.h5'))
    except OSError:
        pass

    # Resize the image with **bicubic** downsampling/upsampling
    resize = lambda size: transforms.Resize((size, size), interpolation=InterpolationMode.BICUBIC)

    create_lr = transforms.Compose([resize(384 // scale)])
    to_tensor = transforms.Compose([resize(384), transforms.ToTensor()])

    lr_samples, hr_samples = [], []
    with h5py.File(os.path.join(root_dir, split + '.h5'), 'w') as dataset:
        # Get a sorted list of all files within 'image_dir'
        image_paths = sorted([i for i in os.listdir(image_dir)], key=lambda x: x.split('.')[0])
        for image_path in tqdm(iterable=image_paths, total=len(image_paths), desc="Creating .h5 file"):
            hr_image = Image.open(os.path.join(image_dir, image_path))
            lr_image = create_lr(hr_image) # Bicubic downsampling of HR image

            lr_image = to_tensor(lr_image) # Image to tensor
            hr_image = to_tensor(hr_image) # Image to tensor + upsampling

            if split == 'train':
                k = 32
                # For train dataset, we extract 32x32 image patches with stride
                # of 16. The overlap reduces harsh boundaries in upscaled images
                for i in range(0, 384 - k + 1, 16):
                    for j in range(0, 384 - k + 1, 16):
                        lr_samples.append(lr_image[:, i:i + k, j:j + k].numpy())
                        hr_samples.append(hr_image[:, i:i + k, j:j + k].numpy())
            elif split == 'val':
                # For validation dataset, we just use the full size images
                lr_samples.append(lr_image.numpy())
                hr_samples.append(hr_image.numpy())
        dataset.create_dataset('lr', data=np.array(lr_samples))
        dataset.create_dataset('hr', data=np.array(hr_samples))

In [ ]:
create_h5_dataset('./', './data/images/HR/', split='train', scale=3)
create_h5_dataset('./', './data/images/HR/', split='val', scale=3)

Creating .h5 file: 100%|██████████| 100/100 [00:02<00:00, 47.03it/s]


### Define Train and Evaluation Methods

In [ ]:
from tqdm import tqdm

def train(model, train_loader, val_loader, optimizer, criterion, device, num_epochs):
    """
    Train the model on the training set and evaluate it on the validation set every epoch.
    """
    model = model.to(device) # Place model on device
    loss_history = []
    for epoch in range(num_epochs):
        model.train()  # Set model to training mode

        # Use tqdm to display a progress bar during training
        with tqdm(total=len(train_loader), desc=f'Epoch {epoch + 1}/{num_epochs}') as pbar:
            for inputs, labels in train_loader:
                # Move inputs and labels to device
                inputs = inputs.to(device)
                labels = labels.to(device)
                
                optimizer.zero_grad()  # Zero out gradients      
                logits = model(inputs) # Compute the logits and loss
                loss = criterion(logits, labels)
                
                loss.backward()  # Backpropagate the loss
                optimizer.step() # Update the weights  
                pbar.update(1)   # Update the progress bar
                pbar.set_postfix(loss=loss.item())
        
        # Evaluate the model on the validation set
        avg_losses = evaluate(model, val_loader, [criterion, psnr, ssim], device)
        loss_history.append(avg_losses)
        print(f'Validation set: average psnr/ssim = {avg_losses[1]:.4f}/{avg_losses[2]:.4f}')
        
        # Save model weights creating a backup of previously saved
        torch.save(model.state_dict(), os.path.join(root_dir, 'weights', f'srcnn_weights_epoch{epoch}.pth'))
    return loss_history



def evaluate(model, test_loader, criterions, device):
    """
    Evaluate the model on the test set.
    """
    model.eval()  # Set model to evaluation mode
    
    with torch.no_grad():
        total_losses = [0.0]*len(criterions)
        
        for inputs, labels in test_loader:
            # Move inputs and labels to device
            inputs = inputs.to(device)
            labels = labels.to(device)

            logits = model(inputs).clamp(0.0, 1.0)
            for i in range(len(criterions)):
                loss = criterions[i](logits, labels)
                total_losses[i] += loss

    # Compute the average loss and accuracy
    avg_losses = [0.0]*len(criterions)
    for i in range(len(criterions)):
        avg_losses[i] = (total_losses[i] / len(test_loader)).item()
                
    return tuple(avg_losses)

#####**Testing the Dataset** 
We display randomly selected low-resolution samples along with their high-resolution counterpart. Later we will compare these with the super-resolution counterpart generated by the SRCNN model.

In [ ]:
import matplotlib.pyplot as plt

example_dataset = SuperResolution(os.path.join(root_dir, 'data'))
figure = plt.figure(figsize=(20, 7.75))
cols, rows, samples = 2, 5, []
for _ in range(5):
    sample_idx = torch.randint(len(example_dataset), size=(1,)).item()
    samples.append(example_dataset[sample_idx])

for i in range(1, rows * cols + 1):
    img = samples[i - 1][0] if i < rows + 1 else samples[i % rows - 1][1]
    figure.add_subplot(cols, rows, i)
    plt.axis("off")
    plt.imshow(tensor_to_image(img))
plt.show()

## SRCNN



### Define the SRCNN Model
We will create our SRCNN model based on the kernel sizes/depths with a "good performance-speed trade-off" as described in Dong et al---that is, with filter sizes $k_1=32$, $k_2=64$, $k_3=3$, with depths $d_1=9$, $d_2=5$, $d_3=5$ for the three layers of the model.

In [ ]:
from torch import nn

class SRCNN(nn.Module):
    def __init__(self):
        super(SRCNN, self).__init__()
        self.features = nn.Sequential(
            nn.Conv2d(3,  64, kernel_size=9, stride=1, padding=9 // 2),
            nn.Conv2d(64, 32, kernel_size=5, stride=1, padding=5 // 2),
            nn.Conv2d(32, 3,  kernel_size=5, stride=1, padding=5 // 2),
            nn.ReLU(True),
        )

    def forward(self, x):
        x = self.features(x)
        return x

### Training the SRCNN Model

In [ ]:
# Define the device to use for training
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
if device == torch.device('cuda'):
    print(f'Using device: {device}. Good to go!')
else:
    print('Please set GPU via Edit -> Notebook Settings.')

Using device: cuda. Good to go!


In [ ]:
from pathlib import Path

# Define the batch size and number of workers
batch_size = 64
num_workers = 2

# Create super resolution train and validation datasets + PyTorch dataloaders
data_root = os.path.join(root_dir, 'data')
srcnn_train_dataset = SuperResolution(data_root, split='train')
srcnn_val_dataset = SuperResolution(data_root, split='val')

srcnn_train_loader = torch.utils.data.DataLoader(
    srcnn_train_dataset, batch_size=batch_size, num_workers=num_workers, shuffle=True)
srcnn_val_loader = torch.utils.data.DataLoader(
    srcnn_val_dataset, batch_size=batch_size, num_workers=num_workers, shuffle=False)

# Define the model, optimizer, and criterion (loss_fn)
srcnn = nn.DataParallel(SRCNN())

# SRCNN Paper uses 1e-4 for the first two conv layers and 1e-5 for the last conv 
# layer. For loss, the paper uses mean squared error.
adam = torch.optim.Adam([
    { 'params': srcnn.module.features[0].parameters() },
    { 'params': srcnn.module.features[1].parameters() },
    { 'params': srcnn.module.features[2].parameters(), 'lr': 1e-5 }
], lr=1e-4)
mse_loss = nn.MSELoss()

In [ ]:
!wget -qN https://github.com/2Retr0/CS188-Final-Project/raw/main/srcnn_pretrained_weights_e200.pth

pretrained = True

In [ ]:
if not pretrained:
    # Train the model for 200 epochs.
    train(srcnn, srcnn_train_loader, srcnn_val_loader, adam, mse_loss, device, num_epochs=200)
else:
    srcnn.load_state_dict(torch.load('srcnn_pretrained_weights_e200.pth'))

### Testing the SRCNN Model
We display randomly selected low-resolution samples along with its super-resolution (SRCNN-generated) and high-resolution (ground-truth) image counterparts.

In [ ]:
def display_samples(zoom_in=False):
    srcnn.eval()

    figure = plt.figure(figsize=(40, 24))
    cols, rows, samples = 3, 5, []
    for _ in range(5):
        sample_idx = torch.randint(len(srcnn_val_dataset), size=(1,)).item()
        (lr_image, hr_image), sr_image = srcnn_val_dataset[sample_idx], None
        with torch.no_grad():
            sr_image = srcnn(lr_image.to(device)).cpu()
        samples.append((lr_image, sr_image, hr_image))

    for i in range(1, rows * cols + 1):
        img = samples[i % rows - 1][(i - 1) // rows]
        if zoom_in:
            img = torchvision.transforms.CenterCrop(100)(img)
        figure.add_subplot(cols, rows, i)
        plt.axis("off")
        plt.imshow(tensor_to_image(img))
    plt.show()

In [ ]:
display_samples(zoom_in=False)

In [ ]:
display_samples(zoom_in=True)

NameError: ignored

<Figure size 2880x1728 with 0 Axes>

##### **Using Our Own Images**
Now the fun part! We want to test the model on our own images to see how well we can super-resolve them.

In [ ]:
# resize = lambda size: transforms.Resize((size, size), interpolation=InterpolationMode.BICUBIC)
# to_tensor = transforms.Compose([resize(384), transforms.ToTensor()])

# samples = []

# figure = plt.figure(figsize=(24, 15))

# for _, _, images in os.walk('./our_images'):
#   for image_path in images:
#     img = Image.open(os.path.join('./our_images', image_path))
#     img = img.convert('RGB')
#     img = to_tensor(img)
    
#     with torch.no_grad():
#       sr_image = srcnn(img.to('cuda')).cpu()
#     # print(img.shape, sr_image.shape)
#     samples.append((img, sr_image))


# cols, rows = 2, len(samples)

# for i in range(1, rows * cols + 1):
#     img = samples[i % rows - 1][(i - 1) // rows]
#     figure.add_subplot(cols, rows, i)
#     plt.axis("off")
#     plt.imshow(tensor_to_image(img))
# plt.show()
